### Importing The Required Libraries:

In [1]:
import warnings
warnings.filterwarnings('ignore')

import tensorflow as tf
from tensorflow.keras.layers import Embedding, LSTM, Dense
from tensorflow.keras.models import Sequential
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.preprocessing.text import Tokenizer

tf.__version__
sess = tf.compat.v1.Session(config=tf.compat.v1.ConfigProto(log_device_placement=True))
from tensorflow.compat.v1 import ConfigProto
from tensorflow.compat.v1 import InteractiveSession

config = ConfigProto()
config.gpu_options.allow_growth = True
session = InteractiveSession(config=config)


import pickle
import numpy as np

import os
import os.path

import string
from itertools import chain

from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras.callbacks import ReduceLROnPlateau
from tensorflow.keras.callbacks import TensorBoard
from tensorflow.keras.models import load_model


Device mapping:
/job:localhost/replica:0/task:0/device:GPU:0 -> device: 0, name: NVIDIA GeForce RTX 2080 SUPER, pci bus id: 0000:05:00.0, compute capability: 7.5



In [2]:

filename = "qa-10M"
tokenizer = pickle.load(open('tokenizer/tokenizer-' + filename + '.pkl', 'rb'))

model = load_model('nextword-'+filename+'.h5')


In [3]:

def Predict_Next_Words(model, tokenizer, text):
    #print(text)
    sequence = tokenizer.texts_to_sequences([text])[0]
    sequence = np.array(sequence)
    res = []
    preds = model.predict(sequence)
    preds1= np.flip(np.argsort(preds,axis=1))
    preds = np.argmax(preds,axis=1)
    for i in range(10):
        res.append((preds1[0][i]))
    #print(len(res))
    predicted_word = ""
    predicted_words = []

    for key, value in tokenizer.word_index.items():
        if value in res:
            predicted_words.append(key)
            #print(key)
            #break

    #print(len(predicted_word))
    return predicted_words


In [15]:
fname = "conv2"

In [16]:
file_path = "data/" + fname + "-cleaned.txt"
if(os.path.exists(file_path)):
    data = open("data/" + fname + "-cleaned.txt", "r", encoding = "utf8")
else:
    file = open("data/" + fname + ".txt", "r", encoding = "utf8")
    lines = []
    l = 0
    for i in file:
        lines.append(i)
        l = l + 1
    if (l > 5):
        print("The First Line: ", lines[0])
        print("The Last Line: ", lines[-1])
    else:
        print(len(lines[0]))
    data = ""

    for i in lines:
        data = ' '. join(lines)

    data = data.replace('\n', '').replace('\r', '').replace('\ufeff', '')

    translator = str.maketrans(string.punctuation, ' '*len(string.punctuation)) #map punctuation to space
    data = data.translate(translator)
    data = data.replace('  ', ' ').replace('  ', ' ')

    data = ''.join(filter(lambda x: not x.isdigit(), data))

    with open("data/" + fname + "-cleaned.txt", 'w', encoding='utf-8') as output:
        output.write(data)

data[:360]

69


'Of course I did Real Madrid played really well and deserved to win Really I thought Real had more control over the game and created more scoring opportunities I can t deny that Messi is a great player but I still think Real deserved to win They were more organized and disciplined on the field We ll see about that Real Madrid has a strong team this year and I'

In [17]:
z = set(chain(*(line.split() for line in data.split() if line)))
print(len(z))

unique_words = ' '.join(z)
print(unique_words)

73
played field strong always created really Really course opportunities this top see were has Of Agreed going beat win I go they great Real and deny still who player s organized control exciting no scoring to out head team comes about It two did be had re Madrid They We that disciplined but ll on a over teams matter deserved the game these more t Messi thought is year tough think can well


In [18]:
sequence_data = tokenizer.texts_to_sequences([data])[0]
sequence_data[:10]


[188, 2091, 1868, 31, 189, 9454, 4194, 65, 47, 28]

In [19]:
vocab_size = len(tokenizer.word_index) + 1
print(vocab_size)

27784


In [20]:
model_new = model

checkpoint = ModelCheckpoint("nextword-"+fname+".h5", monitor='loss', verbose=1,
    save_best_only=True, mode='auto')

reduce = ReduceLROnPlateau(monitor='loss', factor=0.2, patience=3, min_lr=0.0001, verbose = 1)

logdir='logsnextword'+fname
tensorboard_Visualization = TensorBoard(log_dir=logdir)

model_new.compile(loss="categorical_crossentropy", optimizer=Adam(learning_rate=0.001))

In [23]:
sequences = []
for i in range(1, int(len(sequence_data))):
    words = sequence_data[i-1:i+1]
    sequences.append(words)

#print("The Length of sequences are: ", len(sequences))
sequences = np.array(sequences)
#sequences[:10]


X = []
Y = []

for i in sequences:
    X.append(i[0])
    Y.append(i[1])

X = np.array(X)
Y = np.array(Y)

Y = to_categorical(Y, num_classes=vocab_size)
X[:5]
Y[:5]


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [24]:
model_new.fit(X, Y, epochs=50, batch_size=64, callbacks=[checkpoint, reduce, tensorboard_Visualization])


Epoch 1/50
2/2 [==============================] - 4s 501ms/step - loss: 23.1360

Epoch 00001: loss improved from inf to 23.13600, saving model to nextword-conv2.h5
Epoch 2/50
2/2 [==============================] - 0s 16ms/step - loss: 19.3172

Epoch 00002: loss improved from 23.13600 to 19.31719, saving model to nextword-conv2.h5
Epoch 3/50
2/2 [==============================] - 0s 79ms/step - loss: 16.4309

Epoch 00003: loss improved from 19.31719 to 16.43091, saving model to nextword-conv2.h5
Epoch 4/50
2/2 [==============================] - 0s 79ms/step - loss: 14.3974

Epoch 00004: loss improved from 16.43091 to 14.39737, saving model to nextword-conv2.h5
Epoch 5/50
2/2 [==============================] - 0s 16ms/step - loss: 12.9738

Epoch 00005: loss improved from 14.39737 to 12.97377, saving model to nextword-conv2.h5
Epoch 6/50
2/2 [==============================] - 0s 69ms/step - loss: 11.9668

Epoch 00006: loss improved from 12.97377 to 11.96676, saving model to nextword-conv2

2/2 [==============================] - 0s 94ms/step - loss: 3.4710

Epoch 00050: loss improved from 3.69458 to 3.47105, saving model to nextword-conv2.h5


In [6]:

text = "Obviously";
export = Predict_Next_Words(model, tokenizer, text)
print(export)

print(len(tokenizer.word_index.items()))


['wow', 'thanks', 'tv', 'its', 'floppy', 'eminem', 'say', 'kick', 'hasn', 'gps']
27783


In [14]:
for key, value in tokenizer.word_index.items():
    export = Predict_Next_Words(model, tokenizer, key)
    print(str(value) + "\t" + key + "\t" + "\t".join(export))

1	phd	wow	thanks	tv	gallons	oooh	into	politicians	hasn	le	stephs
2	myspace	thanks	tv	mp	only	eminem	oooh	must	toy	politicians	hasn
3	lebron	the	thanks	nike	ha	mp	right	interesting	perhaps	politicians	hasn
4	you	nike	tv	kpop	right	co	postage	sundays	re	colbert	monfils
5	wow	wow	thanks	tv	right	uk	oooh	perhaps	cricket	hasn	weekend
6	youtube	wow	thanks	tv	spacex	eminem	states	toy	perhaps	politicians	jackass
7	the	lebron	wow	thanks	tv	spacex	states	sundays	perhaps	politicians	hasn
8	lol	thanks	nike	ha	mp	spacex	eminem	oooh	perhaps	unbelievable	politicians
9	like	wow	tv	mp	interesting	spacex	eminem	states	sundays	politicians	hasn
10	think	thanks	interesting	spacex	toy	perhaps	nextflix	unbelievable	politicians	depends	cmt
11	something	wow	thanks	tv	ha	right	year	oooh	must	politicians	hasn
12	too	tv	bill	curtis	they	gallons	sat	toy	cruise	stealing	dolls
13	have	wow	thanks	tv	sure	mp	only	eminem	oooh	politicians	hasn
14	mcdonald	thanks	tv	ha	mp	only	eminem	oooh	politicians	hasn	away
15	thanks	

118	pac	thanks	tv	ha	mp	eminem	oooh	toy	perhaps	politicians	hasn
119	gb	wow	thanks	tv	its	ha	amazing	eminem	politicians	hasn	netherlands
120	hit	thanks	tv	mp	amazing	only	eminem	oooh	must	politicians	hasn
121	speaking	nike	tv	who	space	am	donald	way	mother	constituents	business
122	goat	tv	sure	mb	eminem	must	tesla	toy	cathode	politicians	wimbledon
123	redford	thanks	nike	got	ha	spacex	knew	starship	climate	to	politicians
124	police	thanks	tv	its	mp	only	eminem	oooh	must	politicians	hasn
125	when	thanks	nike	tv	bill	its	ha	mp	say	hasn	irish
126	right	wow	the	thanks	nike	tv	right	gallons	hasn	jackass	japan
127	interesting	youtube	bill	everything	mp	postage	only	collinsville	re	iam	few
128	white	wow	thanks	tv	spacex	eminem	into	sundays	toy	politicians	hasn
129	best	wow	thanks	tv	maybe	spacex	banned	toy	perhaps	india	hasn
130	tiny	thanks	tv	royals	amazing	starship	empire	icbm	into	sundays	must
131	globe	tv	how	gallons	floppy	probably	oooh	re	politicians	amazons	hiddleston
132	red	bill	son

233	oops	thanks	tv	mp	amazing	only	oooh	must	politicians	hasn	away
234	dont	the	thanks	tv	only	eminem	oooh	must	say	hasn	mets
235	egot	thanks	don	durst	diff	kick	politicians	last	london	mythology	significance
236	unicef	thanks	tv	mp	eminem	oooh	into	must	toy	politicians	hasn
237	starship	youtube	everything	mp	co	colbert	olivia	few	monfils	barks	outscore
238	wild	wow	nike	tv	eminem	placing	politicians	hasn	cider	youre	terry
239	pet	thanks	tv	mp	amazing	spacex	starship	eminem	states	toy	politicians
240	wonder	nike	tv	right	oooh	sundays	sheep	vr	re	female	hiddleston
241	marvel	wow	nike	tv	right	eve	sheep	hasn	angeles	youre	hiddleston
242	la	tv	imax	sundays	hot	medals	frequency	goodnight	speeding	constance	rambo
243	gallons	nike	tv	space	am	donald	mb	eminem	way	business	wilderness
244	with	wow	tv	gallons	kalakaua	toy	happy	politicians	hasn	scotus	youre
245	lot	wow	thanks	tv	ha	spacex	starship	eminem	oooh	perhaps	contact
246	cops	tv	only	eminem	oooh	must	toy	politicians	hasn	cider	netherlan

348	duncan	lebron	tv	sure	amazonbasics	starship	gallons	empire	toy	romans	wallpaper
349	half	tv	right	hulk	dueling	hes	colorblind	decision	snowbelt	taht	containing
350	longer	wow	tv	how	floppy	re	politicians	hasn	scotus	amazons	sterilize
351	apple	thanks	tv	ha	spacex	eminem	states	oooh	toy	politicians	hasn
352	john	thanks	tv	its	mp	only	eminem	oooh	politicians	hasn	away
353	africa	tv	sure	interesting	must	toy	politicians	hasn	carey	sounded	nuance
354	nasa	sure	mb	creed	must	toy	hasn	cider	curry	carey	netherlands
355	floppy	wow	tv	starship	laurie	sundays	hasn	scotus	angeles	youre	terry
356	probably	wow	thanks	tv	into	sundays	passed	hasn	kunk	break	g
357	homo	wow	thanks	tv	who	spacex	starship	mb	eminem	toy	politicians
358	ice	thanks	tv	tupac	into	politicians	hasn	waters	stapp	cell	hikers
359	snow	tv	mp	year	oooh	must	toy	granddaughter	patrons	boat	webbing
360	mostly	wow	the	thanks	tv	amazing	eminem	oooh	into	politicians	hasn
361	ram	thanks	tv	sure	mp	eminem	states	oooh	into	toy	politicia

465	paid	wow	nike	tv	foxnews	chapo	workaholics	amazons	hiddleston	favortism	collaborate
466	jim	tv	mp	year	eminem	oooh	must	toy	politicians	cider	governors
467	play	thanks	tv	its	oooh	into	sundays	must	sheep	hasn	waters
468	trump	thanks	nike	tv	right	am	sundays	way	mother	hasn	darley
469	kim	wow	thanks	tv	amazing	spacex	only	eminem	oooh	politicians	hasn
470	con	thanks	tv	mp	amazing	only	eminem	oooh	politicians	hasn	away
471	eminem	wow	nike	tv	iphone	sundays	hasn	scotus	angeles	specialized	terry
472	lo	wow	thanks	tv	right	oooh	must	perhaps	unbelievable	politicians	hasn
473	st	wow	youtube	thanks	tv	everything	wonka	creed	few	slightly	emperor
474	friends	thanks	tv	mp	only	eminem	oooh	must	toy	politicians	hasn
475	wwi	wow	tv	who	mp	interesting	spacex	eminem	toy	politicians	hasn
476	icbm	nike	tv	right	co	dc	re	iam	heart	contest	trust
477	uk	lebron	sure	imax	amazonbasics	starship	horrible	toy	romans	hasn	helpful
478	paypal	thanks	tv	mp	only	eminem	oooh	must	unbelievable	politicians	hasn
479	

...

27300	zootopia	wow	thanks	tv	its	amazing	floppy	eminem	oooh	say	hasn
27301	eragon	wow	thanks	tv	ha	mp	only	eminem	oooh	politicians	hasn
27302	investors	thanks	tv	its	ha	mp	only	eminem	oooh	politicians	hasn
27303	compartment	wow	thanks	tv	its	amazing	eminem	oooh	must	politicians	hasn
27304	outlaws	thanks	tv	ha	mp	amazing	only	eminem	oooh	politicians	hasn
27305	references	thanks	tv	its	amazing	only	eminem	oooh	say	hasn	netherlands
27306	makeup	wow	thanks	tv	mp	spacex	eminem	oooh	toy	politicians	hasn
27307	austen	thanks	tv	mp	only	eminem	oooh	must	politicians	hasn	away
27308	crimes	wow	thanks	tv	its	say	hasn	mets	powerwall	away	gps
27309	encoding	thanks	tv	mp	amazing	only	eminem	oooh	must	politicians	hasn
27310	inclined	thanks	tv	mp	only	oooh	must	toy	unbelievable	politicians	hasn
27311	borne	wow	thanks	tv	its	amazing	eminem	oooh	say	politicians	hasn
27312	malevolent	thanks	tv	interesting	spacex	only	eminem	oooh	toy	politicians	hasn
27313	rioting	thanks	tv	mp	interesting	amazing	only	oooh

27412	allers	thanks	tv	ha	mp	only	eminem	oooh	toy	politicians	hasn
27413	inmates	thanks	tv	eminem	oooh	sundays	must	toy	politicians	hasn	cider
27414	columbus	the	thanks	tv	only	eminem	oooh	must	politicians	hasn	netherlands
27415	parameters	thanks	tv	ha	mp	only	oooh	must	perhaps	politicians	hasn
27416	clearing	wow	thanks	tv	amazing	eminem	oooh	toy	nextflix	politicians	hasn
27417	cathedrals	thanks	tv	its	mp	only	eminem	oooh	must	politicians	hasn
27418	chambered	wow	thanks	spacex	doo	sundays	toy	perhaps	bohemian	speak	politicians
27419	briefer	the	thanks	tv	mp	amazing	only	oooh	must	politicians	hasn
27420	dian	thanks	tv	ha	mp	only	eminem	oooh	toy	politicians	hasn
27421	embarrassment	wow	thanks	tv	amazing	spacex	eminem	oooh	tesla	politicians	hasn
27422	israely	wow	thanks	tv	spacex	eminem	sundays	toy	perhaps	politicians	hasn
27423	confused	wow	thanks	nike	tv	interesting	into	say	politicians	hasn	mets
27424	strap	thanks	tv	mp	only	eminem	oooh	into	must	politicians	hasn
27425	arested	wow	tv	h

27525	gel	wow	nike	tv	states	happy	steamboat	bohemian	politicians	amazons	hiddleston
27526	sentiment	wow	thanks	tv	amazing	spacex	eminem	say	politicians	hasn	gps
27527	douglas	wow	thanks	tv	ha	spacex	eminem	oooh	toy	politicians	hasn
27528	reinvented	wow	thanks	tv	spacex	eminem	sundays	nextflix	kick	politicians	hasn
27529	griping	thanks	tv	ha	eminem	oooh	perhaps	kick	politicians	hasn	amazons
27530	chappie	thanks	tv	its	mp	eminem	oooh	must	politicians	hasn	honest
27531	skipped	thanks	tv	amazing	only	eminem	oooh	into	must	politicians	hasn
27532	foxx	wow	thanks	nike	tv	spacex	eminem	oooh	tesla	politicians	hasn
27533	catchphrase	the	thanks	tv	sure	oooh	into	must	toy	politicians	hasn
27534	entertainers	thanks	tv	ha	mp	only	eminem	oooh	must	politicians	hasn
27535	persona	thanks	tv	mp	only	oooh	must	toy	politicians	hasn	cider
27536	suuppose	thanks	tv	its	mp	amazing	only	eminem	oooh	must	politicians
27537	teaches	thanks	tv	ha	mp	amazing	eminem	oooh	must	politicians	hasn
27538	fills	thanks	tv	it

27638	fantasizing	thanks	tv	mp	only	eminem	oooh	must	toy	politicians	hasn
27639	verlander	thanks	tv	right	gallons	must	sheep	hasn	waters	becaus	secrete
27640	rescuers	wow	thanks	tv	ha	mp	amazing	eminem	oooh	politicians	hasn
27641	soonly	the	thanks	tv	mp	oooh	into	must	toy	hasn	cider
27642	endorsing	tv	ha	mp	eminem	oooh	must	toy	politicians	hasn	cider
27643	misconstrued	wow	thanks	tv	eminem	oooh	kick	politicians	hasn	gps	amazons
27644	bucketlist	wow	thanks	tv	eminem	tesla	say	politicians	hasn	mets	gps
27645	herald	tv	interesting	am	body	mb	eminem	oooh	politicians	hasn	netherlands
27646	orbital	the	thanks	tv	oooh	into	must	say	hasn	range	mets
27647	doger	thanks	tv	its	mp	eminem	oooh	must	politicians	hasn	away
27648	humpty	thanks	tv	its	mp	only	eminem	oooh	must	politicians	hasn
27649	occurring	thanks	tv	sure	mp	only	oooh	into	must	politicians	hasn
27650	psyched	thanks	tv	mp	only	eminem	oooh	must	toy	politicians	hasn
27651	symbiosis	wow	thanks	tv	its	floppy	eminem	hasn	powerwall	gps	closes

27751	invite	wow	thanks	tv	amazing	spacex	eminem	oooh	sundays	politicians	hasn
27752	uplink	wow	thanks	tv	amazing	spacex	eminem	oooh	kick	politicians	hasn
27753	grappa	thanks	tv	ha	mp	only	eminem	oooh	toy	politicians	hasn
27754	batson	wow	the	thanks	tv	eminem	oooh	sundays	must	politicians	hasn
27755	cheated	wow	thanks	nike	tv	interesting	spacex	eminem	oooh	politicians	hasn
27756	trademark	wow	thanks	tv	yes	eminem	say	politicians	hasn	mets	gps
27757	entice	wow	thanks	tv	eminem	sundays	toy	politicians	hasn	cider	netherlands
27758	assaults	thanks	tv	ha	mp	amazing	eminem	oooh	must	politicians	hasn
27759	platter	thanks	tv	sure	eminem	oooh	must	toy	politicians	hasn	cider
27760	boldest	wow	thanks	tv	its	amazing	eminem	oooh	must	politicians	hasn
27761	symbolized	thanks	tv	mp	amazing	eminem	oooh	must	toy	politicians	hasn
27762	sore	thanks	tv	mp	only	eminem	oooh	must	toy	politicians	hasn
27763	mismanage	wow	the	thanks	tv	mp	oooh	into	politicians	hasn	mets
27764	levine	wow	thanks	tv	ha	eminem	ooo

In [25]:
for key, value in tokenizer.word_index.items():
    export = Predict_Next_Words(model_new, tokenizer, key)
    print(str(value) + "\t" + key + "\t" + "\t".join(export))

1	phd	wow	the	tv	gallons	oooh	into	more	to	hasn	mets
2	myspace	wow	nike	spacex	eminem	states	toy	we	kleenex	politicians	hasn
3	lebron	youtube	nike	tv	well	bill	spacex	only	sundays	politicians	hasn
4	you	tv	sundays	a	cities	head	colbert	hasn	carnival	numerous	hairbrained
5	wow	thanks	really	ha	starship	uk	oooh	to	toy	perhaps	politicians
6	youtube	wow	thanks	tv	who	spacex	starship	eminem	toy	politicians	jackass
7	the	lebron	tv	spacex	banned	sundays	game	a	see	field	hasn
8	lol	wow	nike	tv	who	mp	spacex	starship	eminem	toy	politicians
9	like	wow	tv	spacex	starship	eminem	sundays	toy	politicians	hasn	afterwords
10	think	wow	the	thanks	nike	tv	they	real	we	armour	ll
11	something	wow	thanks	tv	sure	mp	right	year	oooh	politicians	hasn
12	too	tv	curtis	gallons	toy	i	parents	stealing	netherlands	horrifying	demons
13	have	wow	nike	spacex	states	to	toy	happy	kleenex	politicians	hasn
14	mcdonald	wow	tv	who	ha	eminem	toy	great	kick	politicians	hasn
15	thanks	wow	really	they	spacex	oooh	to	toy	politi

123	redford	thanks	got	really	spacex	knew	starship	should	to	toy	politicians
124	police	the	think	tv	who	eminem	more	great	hasn	mets	netherlands
125	when	wow	the	tv	bill	absolutely	co	sundays	say	politicians	hasn
126	right	wow	tv	they	jackass	s	amazons	japan	decode	montage	collaborate
127	interesting	youtube	the	imax	everything	cup	starship	probably	hot	collinsville	few
128	white	wow	thanks	did	spacex	is	sundays	to	toy	happy	hasn
129	best	wow	thanks	tv	maybe	spacex	banned	sundays	toy	hasn	idea
130	tiny	thanks	tv	they	starship	awww	into	sundays	must	hasn	minecraft
131	globe	nike	tv	globe	floppy	toy	happy	hasn	idea	youre	holgram
132	red	someone	toy	event	see	parents	heart	agreed	netherlands	deny	horrifying
133	ugh	wow	tv	and	who	spacex	starship	toy	we	politicians	control
134	want	wow	thanks	tv	spacex	sundays	toy	politicians	bender	ragtime	expel
135	captcha	the	tv	who	they	eminem	oooh	toy	politicians	hasn	mets
136	spencer	wow	nike	really	spacex	eminem	states	to	toy	politicians	hasn
137	wo

242	la	got	really	toy	male	paris	drake	barks	coupling	humiliate	trailers
243	gallons	got	really	spacex	starship	no	oooh	to	toy	politicians	levi
244	with	wow	thanks	sundays	toy	politicians	hasn	youre	ll	hee	cooling
245	lot	wow	the	tv	ha	spacex	starship	probably	eminem	great	hasn
246	cops	the	tv	did	eminem	states	to	toy	hasn	cider	mets
247	worst	tv	spacex	over	mb	hot	wifi	ticks	lung	workaholics	carnival
248	somebody	the	tv	mp	they	more	to	toy	hasn	mets	netherlands
249	alabama	the	tv	who	eminem	to	great	hasn	mets	team	netherlands
250	library	tv	sure	gallons	sat	oooh	toy	politicians	hasn	amazons	apathetic
251	decaprio	the	thanks	tv	did	who	eminem	more	hasn	mets	away
252	cubs	wow	tv	who	spacex	eminem	states	toy	politicians	hasn	cider
253	founder	tv	over	ram	pretty	hot	hotter	lung	helpful	tale	ferb
254	idk	wow	the	thanks	tv	did	who	eminem	oooh	more	hasn
255	norwegian	wow	the	tv	did	who	eminem	to	great	hasn	mets
256	hulu	the	amazing	co	over	martin	say	great	hasn	materials	harris
257	zuckerbur

365	use	got	really	starship	toy	a	i	secretaries	rourke	drake	coupling
366	cya	wow	the	nike	tv	mp	absolutely	eminem	sundays	say	politicians
367	thomas	wow	nike	spacex	eminem	states	toy	great	politicians	hasn	workaholics
368	yea	youtube	the	really	don	co	should	over	to	hot	bruce
369	liked	thanks	tv	starship	banned	sundays	toy	politicians	hasn	afterwords	despacito
370	postage	tv	curtis	mp	student	chaos	bend	olivia	monfils	barks	inexperienced
371	lions	wow	the	thanks	tv	imax	spacex	over	probably	frequency	politicians
372	dod	wow	the	thanks	tv	did	who	eminem	more	to	hasn
373	cnn	wow	did	spacex	is	sundays	to	toy	happy	hasn	cider
374	legal	tv	reams	irs	overcast	extent	slug	scorned	broncos	theere	circumference
375	am	wow	thanks	tv	maybe	banned	sundays	hasn	scotus	specialized	terry
376	nintendo	wow	sure	well	oooh	politicians	jackass	riddance	away	amazons	imposed
377	robin	the	tv	who	interesting	eminem	toy	politicians	hasn	cider	netherlands
378	crazy	wow	thanks	tv	who	mp	eminem	toy	unfortunately

484	as	tv	got	no	nascar	a	politicians	hopefully	male	troves	bowie
485	awesome	wow	thanks	tv	well	eminem	kalakaua	must	hasn	waters	netherlands
486	gif	wow	the	thanks	tv	who	eminem	to	great	hasn	mets
487	wonka	tv	mb	must	game	see	field	be	win	matter	deny
488	legend	wow	tv	spacex	starship	eminem	states	sundays	politicians	hasn	youre
489	sat	wow	tv	and	sure	spacex	toy	see	politicians	be	win
490	horses	tv	mb	must	event	game	see	be	win	matter	deny
491	miami	the	nike	tv	who	ha	interesting	eminem	oooh	perhaps	nuance
492	not	the	tv	who	mp	eminem	more	to	politicians	hasn	mets
493	kalakaua	tv	sure	amazonbasics	mp	horrible	toy	romans	i	helpful	deny
494	instead	wow	the	tv	who	eminem	to	great	politicians	hasn	mets
495	banned	wow	tv	who	spacex	starship	mb	eminem	toy	politicians	hasn
496	states	youtube	the	tv	imax	imbd	everything	probably	hot	great	few
497	bi	thanks	tv	starship	mb	eminem	banned	sundays	toy	hasn	hopefully
498	omg	wow	the	tv	who	eminem	states	toy	great	kick	hasn
499	list	wow	nike	tv	who

...

27239	armory	wow	the	tv	who	eminem	to	great	politicians	hasn	mets
27240	spontaneity	lebron	thanks	tv	and	spacex	sundays	toy	see	politicians	win
27241	affiliation	the	tv	who	eminem	states	toy	great	politicians	hasn	netherlands
27242	elm	wow	the	nike	spacex	states	toy	happy	kleenex	politicians	hasn
27243	bathrooms	wow	nike	really	they	spacex	eminem	toy	great	politicians	hasn
27244	lipizanner	the	nike	tv	who	interesting	states	toy	kleenex	politicians	hasn
27245	pulverized	wow	the	thanks	tv	did	spacex	eminem	kick	politicians	hasn
27246	gypsies	wow	thanks	nike	tv	did	still	great	hasn	ll	superstar
27247	ascenseur	wow	the	think	tv	did	who	eminem	great	hasn	mets
27248	echelons	wow	the	tv	they	spacex	eminem	states	toy	politicians	hasn
27249	evaporate	wow	the	thanks	tv	did	who	eminem	to	hasn	mets
27250	payer	wow	the	nike	they	spacex	still	to	great	politicians	hasn
27251	guru	wow	the	nike	they	spacex	to	toy	happy	politicians	hasn
27252	nagging	wow	the	thanks	tv	did	spacex	eminem	to	politicians	ha

27357	precusor	wow	who	spacex	eminem	states	toy	we	kick	politicians	hasn
27358	suburb	wow	the	tv	spacex	eminem	states	sundays	toy	politicians	hasn
27359	bragged	wow	the	spacex	eminem	toy	we	perhaps	kick	politicians	hasn
27360	isone	wow	the	tv	did	who	eminem	to	great	hasn	mets
27361	located	wow	tv	they	spacex	eminem	states	toy	kick	politicians	hasn
27362	maimed	wow	the	thanks	tv	did	spacex	eminem	more	politicians	hasn
27363	excel	the	tv	who	eminem	states	great	hasn	mets	jackass	netherlands
27364	wondeer	the	tv	did	who	eminem	toy	hasn	cider	mets	netherlands
27365	megadeath	wow	the	tv	who	spacex	eminem	states	toy	politicians	hasn
27366	minneola	wow	the	tv	they	to	toy	happy	politicians	hasn	mets
27367	fart	wow	the	thanks	tv	did	to	great	politicians	hasn	mets
27368	unwrap	wow	tv	did	spacex	eminem	to	great	politicians	hasn	mets
27369	keyword	the	tv	did	who	more	to	great	hasn	mets	netherlands
27370	unfried	wow	the	thanks	nike	tv	did	spacex	still	to	hasn
27371	agency	wow	the	thanks	tv	did	who	

27476	shinier	wow	the	thanks	did	spacex	eminem	sundays	to	politicians	hasn
27477	wond	wow	the	thanks	tv	who	eminem	great	kick	hasn	mets
27478	dorough	wow	the	thanks	tv	did	into	to	politicians	hasn	mets
27479	balances	the	tv	who	mp	more	great	politicians	hasn	mets	netherlands
27480	notoriety	tv	sure	amazonbasics	starship	gallons	oooh	toy	politicians	hasn	riddance
27481	constructing	wow	the	think	tv	did	eminem	great	kick	politicians	hasn
27482	watchhed	wow	the	tv	spacex	eminem	toy	great	kick	politicians	hasn
27483	publisher	wow	the	thanks	tv	did	eminem	to	hasn	cider	mets
27484	peer	thanks	tv	and	walmart	starship	horrible	politicians	hearts	control	evoulutionary
27485	debacle	wow	the	tv	they	to	toy	happy	politicians	hasn	mets
27486	testify	wow	spacex	eminem	states	toy	we	perhaps	constituents	politicians	hasn
27487	buzzer	wow	the	tv	spacex	real	eminem	great	kick	politicians	hasn
27488	oct	wow	nike	tv	mp	spacex	states	say	politicians	colbert	hasn
27489	guangzhou	wow	the	tv	did	who	eminem	to

27594	straightforward	tv	and	sure	starship	mb	eminem	toy	see	netherlands	matter
27595	whatsoever	wow	nike	who	spacex	eminem	toy	happy	we	politicians	hasn
27596	sections	wow	thanks	spacex	is	sundays	toy	happy	kleenex	politicians	hasn
27597	milliom	wow	the	nike	tv	did	to	great	politicians	hasn	mets
27598	lucius	the	think	tv	who	eminem	states	hasn	cider	mets	netherlands
27599	alsoliked	wow	the	tv	did	spacex	still	great	kick	politicians	hasn
27600	mixtape	wow	the	thanks	tv	who	eminem	more	to	hasn	mets
27601	modeling	wow	the	thanks	tv	who	its	eminem	more	hasn	netherlands
27602	ramos	wow	the	tv	did	spacex	eminem	to	politicians	hasn	mets
27603	endorecements	wow	nike	really	spacex	eminem	states	sundays	toy	politicians	hasn
27604	wheni	the	thanks	tv	did	who	eminem	more	to	hasn	mets
27605	dgar	wow	the	tv	they	spacex	eminem	great	kick	politicians	hasn
27606	discourage	wow	the	tv	did	who	eminem	to	great	hasn	mets
27607	aerospace	wow	the	tv	who	they	to	toy	politicians	hasn	mets
27608	wheelbarrel	wo

27713	inexperienced	youtube	tv	mp	right	great	cities	colbert	similar	barks	limited
27714	seeked	wow	nike	really	they	spacex	eminem	states	toy	politicians	hasn
27715	eavesdropping	wow	nike	really	spacex	eminem	states	toy	we	politicians	hasn
27716	racoon	the	nike	they	spacex	states	toy	great	politicians	hasn	mets
27717	equips	wow	the	thanks	tv	did	spacex	eminem	to	politicians	hasn
27718	rhythmy	wow	thanks	nike	did	spacex	is	sundays	toy	politicians	hasn
27719	chicanery	wow	the	tv	who	ha	eminem	states	toy	kick	hasn
27720	delayed	the	tv	who	eminem	states	to	great	politicians	hasn	mets
27721	damage	wow	nike	did	spacex	still	to	toy	happy	politicians	hasn
27722	appeal	wow	the	tv	did	who	eminem	to	politicians	hasn	mets
27723	juices	wow	the	tv	who	eminem	toy	great	kick	politicians	hasn
27724	voyager	wow	thanks	nike	did	they	spacex	toy	politicians	hasn	zucerburg
27725	sewage	wow	the	nike	who	they	states	toy	great	politicians	hasn
27726	overpriced	the	tv	who	eminem	states	toy	hasn	cider	team	nethe